In [ ]:
pip install 

In [4]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import minimize
from statsmodels.nonparametric.smoothers_lowess import lowess
from mpl_toolkits.mplot3d import Axes3D

# Initialize a list to save results
results_list = []
thetas_dict = {}

# Set some Local Folder path
plots_folder = "E:/share/SVI"
if not os.path.exists(plots_folder):
    os.makedirs(plots_folder)

def process_csv_file(filename, ttm_of_interest=5):
    import os
    import pandas as pd
    import numpy as np
    import matplotlib.pyplot as plt
    from scipy.optimize import minimize
    from statsmodels.nonparametric.smoothers_lowess import lowess
    from mpl_toolkits.mplot3d import Axes3D

    # read data:
    df = pd.read_csv(filename)

    """if df.isna().any().any():
        print(f"Skipping {filename} because it contains 'NaN' values.")
        return"""

    #at least 3 ttms observed
    if len(df.columns) <= 3:
        print(f"Skipping {filename} due to having {len(df.columns)} columns.")
        return

    df = df.transpose()

    # Filter out non-numeric indices and convert to integers
    filtered_indices = [int(i) for i in df.index if i.isnumeric()]
    # Convert the list of integers to a numpy array
    row_names_array = np.array(filtered_indices)

    iv_real = df.iloc[1:, :]/100
    iv = iv_real.to_numpy()

    import numpy as np
    import matplotlib.pyplot as plt
    from scipy.optimize import minimize
    from statsmodels.nonparametric.smoothers_lowess import lowess
    from mpl_toolkits.mplot3d import Axes3D

    # SVI model with ttm dependence
    def svi_model(theta, k, tau):
        base_params = np.array(theta[:5])
        ttm_coeffs = np.array(theta[5:])
        a, b, rho, m, sigma = base_params + ttm_coeffs * tau
        return a + b * (rho * (k - m) + np.sqrt((k - m) ** 2 + sigma ** 2))

    def objective_function_grid(theta, k_grid, tau_grid, iv_obs_grid):
        # Specify the ttm of interest, e.g. 5, 9, 14 or 27
        
        iv_obs_grid = iv_obs_grid.reshape(tau_grid.shape[0], k_grid.shape[1])
        iv_model_grid = np.empty_like(iv_obs_grid)

        penalty = 0
        epsilon = 1e-10
        for i in range(tau_grid.shape[0]):
            for j in range(k_grid.shape[1]):
                iv_model_val = svi_model(theta, k_grid[i, j], tau_grid[i, j]) / tau_grid[i, j]

                if iv_model_val < -epsilon:
                    penalty += 100000  # Large value. Don't change.
                    iv_model_grid[i, j] = 0
                else:
                    iv_model_grid[i, j] = np.sqrt(max(iv_model_val, 0))

        mse = np.mean((iv_model_grid - iv_obs_grid) ** 2)
        return np.sqrt(mse) + penalty

    # Given data
    ttm = row_names_array
    # ttm of interest, e.g. 5, 9 , 14 or 27
    #ttm_of_interest = 5
    k = df.iloc[0, :].to_numpy()

    # Generate a grid of strike prices for interpolation
    k_new = np.linspace(k.min(), k.max(), 100)  # Grid of moneyness

    # Interpolate IVs at new strike prices for each ttm
    iv_new = np.empty((len(ttm), len(k_new)))
    for i in range(len(ttm)):
        smoothed = lowess(iv[i, :], k, frac=0.3)  # use local polynomial regression
        iv_new[i, :] = np.interp(k_new, smoothed[:, 0], smoothed[:, 1])

    # Linearly interpolate IVs for each strike price with weights
    iv_at_9_weighted = np.empty(len(k_new))
    for i in range(len(k_new)):
        # Calculate weights
        weights = 1 / np.abs(ttm - ttm_of_interest + 1e-10)  # Avoid division by zero
        weights = weights / np.sum(weights)

        # Calculate weighted average
        iv_at_9_weighted[i] = np.average(iv_new[:, i], weights=weights)

    def callback(theta):
        loss = objective_function_grid(theta, k_grid, ttm_grid, iv.ravel())
        print('Loss at current iteration:', loss)

    # Create grid for optimization
    k_grid, ttm_grid = np.meshgrid(k_new, ttm)

    # Define SVI constraints
    def constraint1(theta):
        base_params = np.array(theta[:5])
        ttm_coeffs = np.array(theta[5:])
        values = [base_params[1] + ttm_coeffs[1] * t for t in ttm]
        if any(np.isnan(values)):
            return -1e10
        return min(values)

    def constraint2(theta):
        base_params = np.array(theta[:5])
        ttm_coeffs = np.array(theta[5:])
        values = [1 - abs(base_params[2] + ttm_coeffs[2] * t) for t in ttm]
        if any(np.isnan(values)):
            return -1e10
        return min(values)

    def constraint3(theta):
        base_params = np.array(theta[:5])
        ttm_coeffs = np.array(theta[5:])
        values = [base_params[0] + ttm_coeffs[0] * t + (base_params[1] + ttm_coeffs[1] * t) * (
                    base_params[4] + ttm_coeffs[4] * t) * np.sqrt(1 - (base_params[2] + ttm_coeffs[2] * t) ** 2) for t
                  in ttm]
        if any(np.isnan(values)):
            return -1e10
        return min(values)

    def constraint4(theta):
        base_params = np.array(theta[:5])
        ttm_coeffs = np.array(theta[5:])
        values = [base_params[4] + ttm_coeffs[4] * t for t in ttm]
        if any(np.isnan(values)):
            return -1e10
        return min(values)

    # Create the constraints dictionary
    constraints = [{'type': 'ineq', 'fun': constraint1},
                   {'type': 'ineq', 'fun': constraint2},
                   {'type': 'ineq', 'fun': constraint3},
                   {'type': 'ineq', 'fun': constraint4}]

    # Initialization
    theta_guess = 0.05 * np.random.rand(10)
    max_iterations = 4  # set some max number of iterations to avoid infinite loops
    iteration_count = 0
    # bounds for 10 parameters. Do not change!
    bounds = [(-4, 4), (-50, 18), (-2, 2), (-2, 2), (-0.5, 1), (-50, 50), (-50, 50), (-2, 2), (-2, 2), (-2, 0.5)]
    lower_bounds = np.array([bound[0] for bound in bounds])
    upper_bounds = np.array([bound[1] for bound in bounds])

    while iteration_count < max_iterations:
        iteration_count += 1

        optimized_thetas = []
        losses = []

        # Iterative Optimization
        for _ in range(10):
            # Vectorized check if thetas are within bounds. If not, set to 0.
            out_of_bounds = (theta_guess < lower_bounds) | (theta_guess > upper_bounds)
            theta_guess[out_of_bounds] = 0

            result = minimize(objective_function_grid, theta_guess, args=(k_grid, ttm_grid, iv_new.ravel()),
                              constraints=constraints, method='SLSQP', bounds=bounds)

            optimized_thetas.append(result.x)
            losses.append(result.fun)  # Assuming result.fun contains the final loss, adjust if not

            # Update the theta_guess for the next iteration
            theta_guess = result.x + 0.02 * np.random.rand(10)

        # Review Results
        best_iteration = np.argmin(losses)
        best_thetas = optimized_thetas[best_iteration]
        best_loss = losses[best_iteration]

        print(f"Best Thetas from Iteration {best_iteration + 1}: {best_thetas}")
        print(f"Lowest Loss: {best_loss}")

        # Compute observed IVs
        y_obs = iv_new.ravel()  # Flattening the matrix for calculation ease

        # Compute predicted IVs using best_thetas
        y_pred = np.array([np.sqrt(svi_model(best_thetas, k, t) / t) for t in ttm for k in k_new])

        # Calculate SS_res
        SS_res = np.sum((y_obs - y_pred) ** 2)

        # Calculate SS_tot
        SS_tot = np.sum((y_obs - y_obs.mean()) ** 2)

        # Calculate R^2
        R2 = 1 - (SS_res / SS_tot)

        print(f"Coefficient of Determination (R^2): {R2:.4f}")

        # Check the R^2 value
        if R2 >= 0.97:
            break
        else:
            print("R^2 is below 0.8, rerunning the optimization...")

    # Now, let's check if the constraints are satisfied at theta_optimized
    print("Constraint 1:", constraint1(best_thetas))
    print("Constraint 2:", constraint2(best_thetas))
    print("Constraint 3:", constraint3(best_thetas))
    print("Constraint 4:", constraint4(best_thetas))

    # Now you can get the predicted IV for e.g. ttm=9 using the SVI model
    k_full = np.linspace(-1, 1, 201)  # Grid of moneyness
    iv_svi_at_9 = np.sqrt(svi_model(best_thetas, k_full, ttm_of_interest) / ttm_of_interest)

    iv_svi_at_9_dict = {f"{k:.4f}": iv for k, iv in zip(k_full, iv_svi_at_9)}
    results_entry = {'Date': filename, 'R2': R2}
    results_entry.update(iv_svi_at_9_dict)
    results_list.append(results_entry)

    thetas_dict[filename] = best_thetas



In [5]:
# Path to read in the IV Matrix files for each day. Use the moneyness folder in the github.
path = "E:/share/SVI/IV/moneyness"
os.chdir(path)

# Iterate over all CSV files in the directory.
# This is the main loop that processes each CSV file.
# I did it on the remote server. It might take some time to estimate all the IVs and parameters, run over night.
# Suggestion: just run the loop for a couple of days to see how it all works.
for filename in os.listdir(path):
    if filename.endswith('.csv') and filename.startswith('IV'):
        print(f"Processing {filename}...")
        # Process the current CSV file
        process_csv_file(filename, ttm_of_interest=14)

# Convert the results list to a dataframe and save to a new CSV
results_df = pd.DataFrame(results_list)
# Convert the dictionary to a DataFrame
df_thetas = pd.DataFrame(thetas_dict).T
# Name columns as per the SVI model parameters
df_thetas.columns = ['a', 'b', 'rho', 'm', 'sigma', 'a_ttm', 'b_ttm', 'rho_ttm', 'm_ttm', 'sigma_ttm']

# Save the results to CSV. Use some local folder of yours.
df_thetas.to_csv('E:/share/SVI/paras14b.csv', index=True)
results_df.to_csv('E:/share/SVI/svi_iv_and_r2_results14b.csv', index=False)


Processing IV_matrix_2017-07-01.csv...
Skipping IV_matrix_2017-07-01.csv due to having 3 columns.
Processing IV_matrix_2017-07-02.csv...
Skipping IV_matrix_2017-07-02.csv due to having 3 columns.
Processing IV_matrix_2017-07-03.csv...
Skipping IV_matrix_2017-07-03.csv due to having 3 columns.
Processing IV_matrix_2017-07-04.csv...
Skipping IV_matrix_2017-07-04.csv due to having 3 columns.
Processing IV_matrix_2017-07-05.csv...
Skipping IV_matrix_2017-07-05.csv due to having 3 columns.
Processing IV_matrix_2017-07-06.csv...
Skipping IV_matrix_2017-07-06.csv due to having 3 columns.
Processing IV_matrix_2017-07-07.csv...
Skipping IV_matrix_2017-07-07.csv due to having 3 columns.
Processing IV_matrix_2017-07-08.csv...
Skipping IV_matrix_2017-07-08.csv due to having 3 columns.
Processing IV_matrix_2017-07-09.csv...
Skipping IV_matrix_2017-07-09.csv due to having 3 columns.
Processing IV_matrix_2017-07-10.csv...
Skipping IV_matrix_2017-07-10.csv due to having 3 columns.
Processing IV_matrix

C:\Users\Guti\AppData\Local\Temp\ipykernel_28516\2469189792.py:136: RuntimeWarning: invalid value encountered in sqrt
  base_params[4] + ttm_coeffs[4] * t) * np.sqrt(1 - (base_params[2] + ttm_coeffs[2] * t) ** 2) for t


Best Thetas from Iteration 6: [ 3.84657890e+00  7.48279813e+00 -6.52827080e-01 -1.07592021e-01
 -9.84893859e-02  5.25763767e-01  4.47774945e-01  6.71223911e-03
  4.04680611e-03  5.47163255e-03]
Lowest Loss: 0.06655164288195924
Coefficient of Determination (R^2): 0.5482
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 9: [ 3.82921230e+00  9.69233298e+00 -6.47059056e-01 -1.14638389e-01
 -1.11170476e-01  5.20481989e-01  3.80725804e-01  6.37950566e-03
  4.22883361e-03  6.17669812e-03]
Lowest Loss: 0.06611724723542894
Coefficient of Determination (R^2): 0.5541
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 9: [ 3.40997595e+00  1.10586634e+01 -6.38689346e-01 -1.13498376e-01
 -1.15220917e-01  5.36273693e-01  3.31271253e-01  5.95140923e-03
  4.16468559e-03  6.40116204e-03]
Lowest Loss: 0.06598695023613926
Coefficient of Determination (R^2): 0.5558
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 9: [ 3.10034619e+00

C:\Users\Guti\AppData\Local\Temp\ipykernel_28516\2469189792.py:136: RuntimeWarning: invalid value encountered in sqrt
  base_params[4] + ttm_coeffs[4] * t) * np.sqrt(1 - (base_params[2] + ttm_coeffs[2] * t) ** 2) for t


Best Thetas from Iteration 1: [ 2.24985690e+00  1.80000000e+01 -1.38016880e+00  2.00000000e+00
  1.00000000e+00 -5.94890931e-01 -9.63743503e-02  1.73494634e-02
 -1.73874093e-01  7.93713186e-02]
Lowest Loss: 0.13049792590548356
Coefficient of Determination (R^2): 0.3869
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 10: [ 4.00000000e+00  6.21398972e+00 -2.16991785e-01  3.72801696e-01
  2.53312725e-01 -2.79720280e-02  1.83959976e+00 -4.11454416e-03
 -2.06507492e-02 -1.77141766e-03]
Lowest Loss: 0.06564985892325739
Coefficient of Determination (R^2): 0.8448
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 1: [ 4.00000000e+00  7.56314266e+00 -2.00727183e-01  3.83170706e-01
  2.52469664e-01 -2.79720280e-02  1.76123012e+00 -4.19469407e-03
 -2.09563976e-02 -1.76552213e-03]
Lowest Loss: 0.06566954284816308
Coefficient of Determination (R^2): 0.8447
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 2: [ 2.17732084e+0

...

C:\Users\Guti\AppData\Local\Temp\ipykernel_28516\2469189792.py:136: RuntimeWarning: invalid value encountered in sqrt
  base_params[4] + ttm_coeffs[4] * t) * np.sqrt(1 - (base_params[2] + ttm_coeffs[2] * t) ** 2) for t


Best Thetas from Iteration 4: [ 0.64750977  1.61672675 -0.59040925  0.02168264  0.06639814 -0.25810691
  4.80056706 -0.01572838 -0.01995336  0.01060269]
Lowest Loss: 0.060697959595071724
Coefficient of Determination (R^2): 0.9515
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 7: [ 0.70712744  1.61704662 -0.59311104  0.01663339  0.07771359 -0.33244425
  5.01097401 -0.01535128 -0.02031968  0.0106977 ]
Lowest Loss: 0.0606642804027233
Coefficient of Determination (R^2): 0.9516
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 10: [ 0.72432049  1.46740811 -0.59107784  0.02252029  0.06410383 -0.27012665
  4.82453176 -0.01567598 -0.02009871  0.01086346]
Lowest Loss: 0.060615290357376624
Coefficient of Determination (R^2): 0.9517
R^2 is below 0.8, rerunning the optimization...
Best Thetas from Iteration 8: [ 4.00000000e+00 -1.59823034e+01 -6.24730746e-01  4.90582232e-02
  6.87388454e-02 -1.15278886e+00  9.44990661e+00 -1.50256715e-02
 -3.110

C:\Users\Guti\AppData\Local\Temp\ipykernel_28516\2469189792.py:136: RuntimeWarning: invalid value encountered in sqrt
  base_params[4] + ttm_coeffs[4] * t) * np.sqrt(1 - (base_params[2] + ttm_coeffs[2] * t) ** 2) for t


Best Thetas from Iteration 10: [ 0.98179645  4.48762893 -0.71347429 -0.07874292  0.09809168 -0.65081189
  7.01292697 -0.00949955 -0.01877688  0.0106306 ]
Lowest Loss: 0.050150608135509187
Coefficient of Determination (R^2): 0.9778
Constraint 1: 25.526409830835107
Constraint 2: 0.12503330721635708
Constraint 3: 1.2538543975392997
Constraint 4: 0.12998346263824415
Processing IV_matrix_2022-11-30.csv...
Skipping IV_matrix_2022-11-30.csv due to having 3 columns.
Processing IV_matrix_2022-12-01.csv...
Skipping IV_matrix_2022-12-01.csv due to having 3 columns.
Processing IV_matrix_2022-12-02.csv...
Skipping IV_matrix_2022-12-02.csv due to having 3 columns.
Processing IV_matrix_2022-12-03.csv...
Skipping IV_matrix_2022-12-03.csv due to having 3 columns.
Processing IV_matrix_2022-12-04.csv...
Skipping IV_matrix_2022-12-04.csv due to having 3 columns.
Processing IV_matrix_2022-12-05.csv...
Skipping IV_matrix_2022-12-05.csv due to having 3 columns.
Processing IV_matrix_2022-12-06.csv...
Skipping

OSError: Cannot save file into a non-existent directory: '\Users\irtg\同步空间\Pricing_Kernel\EPK\matlab_code_for_BTC\SVI'